In [1]:
!pip install confluent_kafka sseclient


[notice] A new release of pip is available: 23.2.1 -> 25.3
[notice] To update, run: python3 -m pip install --upgrade pip


In [2]:
from confluent_kafka import SerializingProducer, DeserializingConsumer
from confluent_kafka.serialization import StringSerializer, StringDeserializer
from confluent_kafka.admin import AdminClient, NewTopic
from uuid import uuid4
import sys, random

brokers = "kafka1:9092"

In [3]:
pconf = {
    'bootstrap.servers': brokers,
    'partitioner': 'murmur2_random',
    'key.serializer': StringSerializer('utf_8'),
    'value.serializer':  StringSerializer('utf_8')
}

In [4]:
p = SerializingProducer(pconf)

In [5]:
stocks = "stocks.csv"

In [6]:
from datetime import datetime  
  #2023-10-13T08:16:13Z

def construct_stock(row):
    time_stamp = time.time()
    date_time = datetime.fromtimestamp(time_stamp)
    str_date_time = date_time.strftime("%Y-%m-%dT%H:%M:%SZ")

    # skip row if empty price or n_shares
    if row[2] == '' or row[5] == '':
        return None  # or I can log the error

    stock = {
        "name": row[6],
        "price": float(row[2]),
        "n_shares": int(row[5]),
        "timestamp": str_date_time
    }
    return stock

In [ ]:
import csv, json
import time
n = 0
with open(stocks) as csv_file:
    csv_reader = csv.reader(csv_file, delimiter=',')
    try:
        for row in csv_reader:
            #if n == 100:
             #  break
            stock = construct_stock(row)
            if stock is None: #
                continue  # jump raw with None 
            print(stock)
            p.produce('stock', value=json.dumps(stock))
            p.poll(0)
            p.flush()
            time.sleep(0.01)
            #n = n + 1
    except BufferError:
        sys.stderr.write('%% Local producer queue is full (%d messages awaiting delivery): try again\n' % len(p))    

{'name': 'ISRG', 'price': 192.6465, 'n_shares': 770940, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'BBT', 'price': 30.8, 'n_shares': 2331836, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'FITB', 'price': 16.63, 'n_shares': 8284724, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'ZION', 'price': 24.57, 'n_shares': 2603143, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'HCP', 'price': 47.08, 'n_shares': 1910622, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'LLY', 'price': 53.91, 'n_shares': 19666635, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'MAC', 'price': 62.01, 'n_shares': 1235821, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'ADBE', 'price': 39.15, 'n_shares': 2490936, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'AZO', 'price': 384.01, 'n_shares': 537986, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'CL', 'price': 54.165, 'n_shares': 3292340, 'timestamp': '2025-11-25T20:26:32Z'}
{'name': 'PPG', 'price': 69.885, 'n_shares': 7626192, 'timestamp': '2025-11-25T20:26:32Z'}
{'n

### Use only if you need to purge all the messages in the queue

In [ ]:
brokers = "kafka1:9092,kafka2:9093"

admin_client = AdminClient({"bootstrap.servers":brokers})
admin_client.delete_topics(topics=['stock'])